In [1]:
import numpy as np
from keras.preprocessing.text import Tokenizer, text_to_word_sequence
from keras.preprocessing.sequence import pad_sequences
from keras.utils import to_categorical
from keras.initializers import Constant
from keras.layers import Input, Dense, GlobalMaxPooling1D
from keras.layers import Conv1D, MaxPooling1D, Embedding, Flatten, Dropout
from keras.models import Model, Sequential
from keras.callbacks import TensorBoard


Using TensorFlow backend.


In [2]:
# getting the features file
path = 'data/task2/'
filename = 'review_features2.tsv'
reviews = []  # list of reviews
label_index = {}  # dictionary of label name, numeric id
labels = []  # list of star ratings
maxlength = 0
with open(path+filename) as f:
    for line in f:
        line = line.split('\t')
        text = line[2].strip()
        # text = text_to_word_sequence(text)
        if len(text) > maxlength:
            maxlength = len(text)
        revid = line[0]
        star = int(float(line[1])) - 1
        label_id = len(label_index)  # ?
        label_index[str(star)] = star + 1
        reviews.append(text)
        labels.append(star)
print("total number of reviews:", len(reviews))
print("total number of labels:", len(labels))
print("max feature_vec length:", maxlength)
# store labels as set
label_set = set(labels)
print(reviews[0])

total number of reviews: 67368
total number of labels: 67368
max feature_vec length: 5000
The gang at Sun Valley Stereo is definitely top notch. Ryan gets right to the point and saw what I was interested in  and we worked together to verify that all the parts were in to upgrade my 2004 RX-8 with a Pioneer 4000NEX touchscreen and back-up camera before I drove 90 minutes for the work. When I first left there was some adjustments needed. They took me back in without hesitation and made everything right. The installer was committed to treating my car like it was his own. He took the extra steps to make it all right  and even fixed the hatch door to my 12-volt socket. Now that's going the extra mile! 6-stars!


In [3]:
# vectorize text features into 2D integer tensor
MAX_NUM_WORDS = 5000
MAX_SEQUENCE_LENGTH = 1000

# tokenizer = Tokenizer(num_words=MAX_NUM_WORDS)
tokenizer = Tokenizer()
tokenizer.fit_on_texts(reviews)

sequences = tokenizer.texts_to_sequences(reviews)
# MAX_SEQUENCE_LENGTH = max([len(s.split()) for s in reviews])
print('Max seq len', MAX_SEQUENCE_LENGTH)

word_index = tokenizer.word_index
MAX_NUM_WORDS = len(word_index) + 1
print('max num words (vocab size)', MAX_NUM_WORDS)
# print("Found {} unique tokens".format(len(word_index)))
print(sequences[0])
data = pad_sequences(sequences, maxlen=MAX_SEQUENCE_LENGTH, padding='post', truncating='post')

labels = to_categorical(np.asarray(labels))
print(labels)
print("Shape of data tensor: ", data.shape)
print("Shape of label tensor: ", labels.shape)


Max seq len 1000
max num words (vocab size) 49607
[1, 6830, 30, 1202, 664, 2823, 11, 76, 262, 679, 1290, 675, 133, 4, 1, 469, 2, 453, 51, 3, 6, 1364, 9, 2, 19, 358, 785, 4, 4149, 16, 33, 1, 754, 34, 9, 4, 2289, 7, 6636, 4514, 582, 14, 5, 8021, 29280, 14301, 2, 49, 41, 3047, 136, 3, 1197, 1383, 204, 10, 1, 69, 54, 3, 84, 249, 57, 6, 89, 2463, 189, 13, 132, 20, 49, 9, 306, 2356, 2, 94, 137, 133, 1, 1984, 6, 4379, 4, 3752, 7, 139, 59, 12, 6, 64, 406, 22, 132, 1, 422, 2650, 4, 111, 12, 33, 133, 2, 79, 351, 1, 10943, 226, 4, 7, 857, 17860, 17861, 127, 385, 122, 1, 422, 1562, 432, 287]
[[0. 0. 0. 0. 1.]
 [1. 0. 0. 0. 0.]
 [0. 0. 0. 0. 1.]
 ...
 [0. 0. 0. 0. 1.]
 [0. 0. 0. 0. 1.]
 [0. 0. 0. 0. 1.]]
Shape of data tensor:  (67368, 1000)
Shape of label tensor:  (67368, 5)


In [4]:
# prepping the embedding matrix
print("Preparing embedding matrix...")
# getting the pre-trained word embeddings
path = '/home/peace/edu/3/'
filename = 'model.txt'  # NLPL dataset 3

embeddings_index = {}
with open(path + filename) as f:
    for line in f:
        word, coefs = line.split(maxsplit=1)
        coefs = np.fromstring(coefs, 'f', sep=' ')
        word = word.split('_')[0]  # get just the word, not POS info
        print(word)
        embeddings_index[word] = coefs

print("Found {} word vectors.".format(len(embeddings_index)))


Preparing embedding matrix...
296630
also
one
first
year
include
two
make
use
time
become
take
play
new
part
know
team
win
season
three
many
later
follow
film
bear
area
member
game
school
family
album
give
name
however
begin
find
second
write
call
number
people
go
well
work
serve
since
city
state
release
work
group
song
may
day
hold
several
see
lead
come
say
series
company
receive
leave
american
system
four
build
population
man
government
May
service
place
September
move
station
start
World
early
January
provide
October
March
June
2010
July
music
band
age
name
country
book
town
line
home
child
August
building
April
November
former
create
appear
December
2011
United::States
die
run
player
village
located
award
student
century
produce
end
another
2012
base
continue
remain
within
2009
local
2008
life
due
world
publish
around
along
club
high
return
event
point
although
February
like
2013
2006
live
woman
2014
10
join
2007
get
form
order
small
show
feature
large
refer
show
son
War
single
dea

link
Saint
jazz
principle
content
distribute
peace
politics
solution
executive
contact
deal
empire
lyric
aspect
regiment
someone
enjoy
generate
green
e.g.
occasion
picture
display
choice
move
unknown
classical
baseball
edge
1918
chairman
help
protection
rating
climate
1951
speech
powerful
ceremony
extensive
Billboard
sense
tribe
celebrate
tour
boundary
urban
bronze
incident
rule
industrial
admit
register
effective
investigation
normal
item
journal
exchange
religion
secure
advance
expansion
captain
hockey
i.e.
treat
best
map
billion
sex
blue
ensure
chief
Historic
Ohio
ultimately
Prince
scottish
organisation
shop
sequence
failure
commit
Love
Sweden
Super
1936
independence
establishment
dog
polish
restaurant
chapter
identity
height
battalion
safety
challenge
1938
enable
reaction
Great
neighborhood
etc.
withdraw
constituency
depict
install
weight
tool
demand
Theatre
Queen
Line
victim
preserve
cancer
architecture
pick
1920
South::Africa
Emperor
garden
requirement
hill
translate
tank
transpo

database
outer
Dance
Montreal
latin
1891
rescue
knock
Bible
tributary
alive
vast
interior
reception
beetle
function
belgian
hip
processing
Liverpool
bid
package
lord
grandfather
conventional
stable
gay
Champions
hunting
unincorporated
execution
rarely
monster
pitch
flood
Football
designation
strategic
phenomenon
cargo
Great::Britain
dissolve
unsuccessful
Player
cave
exposure
so-called
1861
excellent
latest
cd
41
convict
till
ruling
detect
assistant
1888
suitable
1864
FM
slow
specify
1880
inhabit
sr
Christ
retired
helicopter
tape
rescue
Portuguese
du
interpret
border
Third
inscription
attitude
accommodate
Charles
quote
facilitate
advise
sort
else
tissue
resolve
permission
Welsh
Census
NBC
earthquake
premiere
input
en
ferry
fifteen
clan
poll
equivalent
balance
Final
delay
server
refugee
alter
unless
David
snail
German
slope
thirty
question
ministry
sword
sequel
trend
potential
1862
coaching
clear
disambiguation
false
Order
longest
presentation
decorate
thanks
1887
prince
first-class
domi

massacre
De
solely
Revolution
mention
willing
layout
ammunition
naturally
theoretical
exterior
quit
classic
The::New::York::Times
74
Edward
round
76
conviction
girlfriend
Network
expectation
span
transit
crystal
senator
toy
Nevada
butterfly
snake
toll
cabin
assassination
clause
team
Interstate
drinking
discrimination
broadcaster
96
neighbor
la
73
trap
MTV
strict
gospel
neighbourhood
Action
bicycle
House::of::Commons
enact
ship
distant
excavation
escort
hydrogen
71
valid
smooth
whatever
interval
atom
Google
vital
integral
equivalent
anthology
aerial
away
graphic
legacy
model
Wall
adoption
considerably
one
noble
intent
shield
contract
commercial
assumption
ceiling
judicial
freshman
Tony
copyright
Wrestling
associate
embrace
Norfolk
mammal
licence
compensation
terrain
forty
magnitude
intensity
nazi
diesel
arm
magic
ballad
recur
serial
scatter
trainer
sustainable
98
patch
deployment
1849
Bell
revolutionary
badly
guarantee
myth
1840
velocity
Country
Building
finance
vegetable
vowel
onward
i

shark
line-up
pin
acute
Minor
Orange
boyfriend
starter
160
buyer
south-west
v.
gaelic
reference
Louis
cooking
warship
weave
zoo
ill
manual
deed
flourish
oh
3000
Catholic::Church
specialise
NASCAR
regulatory
lecture
mood
purple
15,000
1820
fatal
substrate
lateral
Burma
lodge
dig
bowling
rush
palm
smoke
afterward
Fantasy
kiss
Eurovision
Kim
healthcare
Express
1.2
protester
09
try
Digital
motto
mathematician
Alliance
pine
textbook
attribute
assassinate
angel
Los
seasonal
walk
Rolling
talented
bedroom
stance
disciple
ecclesiastical
Anna
revert
altogether
dose
Manitoba
register
screenwriter
cloth
volcano
citation
broader
selling
reconstruct
aboriginal
Cathedral
pier
monitoring
trafficking
drown
glacier
All-Ireland
anger
suspect
Campbell
next
Operations
tactical
cheese
Rio::de::Janeiro
indication
mere
Daniel
handful
indie
Newfoundland
fitness
inventor
forge
shooter
Distinguished
porch
rna
copy
Apollo
Branch
1,500
Bolivia
catch
promoter
irregular
rite
differentiate
hidden
Number
occurrence
in

...

R.B.
kunus
unkindness
Ottoman::Turkey
upto
Odilo::Globocnik
Alvin::Toffler
Disneyland::Hotel
snug
Karamea
London::Boris::Johnson
depolarisation
John::Cockburn
Monroe::City
tacp
Hillside::Memorial::Park::Cemetery
Ottinger
David::Nolan
Trippi
orthotic
digestif
HAŠK
Kalevipoeg
Milanov
saya
Nullsoft
Widzew
power-broker
Chamaecyparis
vic-ii
West::Siberia
Abiko
tertium
40a
Darnielle
liaison
Rathskeller
Victorian::State::Government
MIPCOM
nazim
Amphidromus
Deportivo::Toluca
Science::Department
William::Harrison::Ainsworth
Frances::Langford
Goffredo
Citronelle
GHMC
multiple-vortex
break-out
Sjumandjaja
Georg::Jacoby
Huayan
Tianxiong::Circuit
National::War::Labor::Board
University::of::Kiev
Middle::States
Betrayer
hyoscyamine
sawtooth
Alacranes
Pepinia
Assembly::of::Representatives
Huddart
WFRV
two-byte
Bank::of::North::America
Nancy::Carroll
PhRMA
Indy::Eleven
back-first
Dares
Staying
Bibl
two-screen
10.56
Aken
dwarfing
Claudia::Karvan
Jia::Zhangke
7:6
Harkleroad
Child::Protective::Services
Ne

mixed-to-negative
Syms
Ngong
Piotrowice
Mbandaka
Mike::Richter
ERDAS
Kakul
d'or
Breslin::Center
Fort::Stotsenburg
Richard::Sorge
waisted
Gorilla::Zoe
gud
Rainville
317,000
El::Hijo::de::Pirata::Morgan
pachycephala
NMM
saurornitholestes
Stade::Lavallois
reverb
Hobgood
Santiago::Creek
half-jokingly
Kalanaur
Prince::Chun
2,512
Strehlow
Hosny
Dirtbombs
New::Smyrna
hydrus
Dulles::Toll::Road
1982-1988
Disklavier
Fretilin
Cork::East
Cerreto
Jokerz
Gull::Island
Tata::Institute::of::Social::Sciences
calamine
Richard::Clapton
Tsugumi
25.84
Béchar::Province
L.::Subramaniam
l'esprit
2,021
blacktop
Lightning::Ridge
Ecovillage
time-reversal
Anthony::Gonzalez
wearied
Cutlass::Supreme
transcoder
courante
John::Oldrid::Scott
Jacob::Javits
panzerarmee
two-tower
Ercilla
altimetry
NACS
Sanad
Bob::Mackie
Citizens::Forces
IRAC
oostende
Brixton::Prison
buzzy
Malatyaspor
Ehrhart
Halcones
St::Richard
Wendy::Doniger
Rotulorum
Kohlmann
Agrupación
Helen::Shapiro
Koroškem
Harvard::Kennedy::School::of::Government
B

Sustainer
q.v.
mid-1600s
Sithu::Kyawhtin
strike-slip
Murgia
hindutva
Central::District::of::Bafq::County
Armendáriz
MetaTrader
Tunde
Coate
2,347
Hester::Thrale
fermata
Hispania::Citerior
floss
Bristoe::Station
Kendal::Town
smoking-related
Xu::Guangqi
rural-based
4-seat
John::Lutz
Li::Gu
Johnny::Olson
Howard::Hampton
lilliputian
Murtoa
δc
Buffalo::Gap
Harlowton
Hawaii::Senate
RCA::Studios
Marco::Beltrami
Winther
Portwood
Phoenix::Foundation
Media::and::Sport::Committee
65th::Army
Ironworkers
half-court
Lachie
Shaz
Eendracht::Aalst
straight-a
Krupskaya
higher
electrocyclic
Caravelles
Straw::Hats
Bergen::County::Technical::Schools
syfy
Patrick::Carney
San::Severino::Marche
Hamilton::Crescent
Acqui::Terme
2,482
Kim::Delaney
non-reserve
Peover
Tosham
Beitbridge
James::Ritchie
Niederrhein
Grendizer
coldzera
theater-goer
Sanyō
Murals
Gunby
Disquisitiones
Semey
screw-driven
berberine
Loza
hepatobiliary
Pennsylvania::Militia
Scott::Baker
Feilden
Hiroshima::University
tiglath-pileser
pdm
Hasinai

Khaira
Avissawella
fica
Salvesen
Kistiakowsky
Wallace::Ford
Borongan
snarling
Nissan::Micra
Charles::Griffin
gsg
Pirenne
John::Sharpe
Fann
Kat::Moon
Zygier
Lajos
eastern
11.55
Ron::Taylor
higher-frequency
bachelorhood
Ballangen
Gangaikonda::Cholapuram
Silvestro
eco
reformatting
Siciliani
sloughing
Keat
Pat::Dye
Moses::Brown
Arts::Council::England
Foggo
Mentorship
ouzel
Phaon
Etana
Grinding
Juskalian
Ballymagauran
capeverdean
Magnolia::Park
ninefold
callin
STAVKA
photorespiration
Courteeners
Pembroke::Castle
Halvorson
Nucci
be-bop
alpha-linolenic
MBD
marburg
Ruggero::Deodato
ICAB
Hersfeld-Rotenburg
Soapbox
Greven
Śāntarakṣita
mechanoid
National::Human::Genome::Research::Institute
Sub-District
Deepfreeze
Kamal::Jumblatt
vinify
Strohm
cobla
Haslet
Vamsy
MoMa
Gentis
Mennen
Douglas::Henshall
Matlin
Fairhill
Hikaru::Sulu
Liu::Ju
Malinalco
George::Herriman
US::Bank
Electoral::Reform::Society
Pannonhalma
Novelas
meristematic
Pharsalus
Scripps::Networks::Interactive
1.200
Fingaz
raúl
connotativ

D-MN
Josuke
Bayerisches
Heathman
Princeton::Seminary
Santa::Maria::River
John::Malone
Levison
spiritualize
Kroni
Stephen::Johnson
Meredith::College
St::Thomas::Aquinas
Gianluca
Board::of::Estimate
Banu::Kilab
Ministry::of::Environmental::Protection
Hodgenville
LLF
Exponential
Anti-Federalist
Wentzville
syndecan
C-Note
Leeds::Beckett::University
Michigan::National::Guard
graver
cranesbill
Trerice
inga
Shamkir::Rayon::of::Azerbaijan
Michael::Hurley
Socialist::Republic::of::Romania
1/n
lewis
monkeypox
inform
Seven::Nation::Army
Simon::Bates
buxwv
Frances::Farmer
pastille
Dontrelle::Willis
bad-ass
Pat::Spillane
sastra
Badoon
1981-1987
outstay
FC::Metalurh::Zaporizhya
Great::Wagon::Road
Zdeněk::Zeman
40k
Butai
Smoky::River
Chieveley
disintegrated
GKS::Bełchatów
infilled
Feightner
Zakuani
Stephen::McNally
Joe::Camilleri
Białowieża::Forest
2,469
Loftleiðir
cvh
bernese
Boncourt
Karatantcheva
Henry::Savile
freebase
tachyonic
non-humanoid
Kingdom::of::Israel
f-series
John::Herron
10-person
Peter

In [5]:
print(embeddings_index['also'])

[-1.01210e-02 -4.52020e-02 -6.56090e-02  1.51320e-02  6.74120e-02
  6.74570e-02  5.20000e-03 -1.53164e-01 -5.06380e-02 -8.14710e-02
  5.39710e-02  7.48610e-02 -6.22350e-02  9.15840e-02 -4.86010e-02
 -2.32140e-02  5.27670e-02 -7.68460e-02 -3.32290e-02 -7.59500e-03
 -5.47150e-02  6.45960e-02 -1.06300e-02 -6.51530e-02 -3.14560e-02
  5.20150e-02  5.63600e-03 -4.15790e-02  4.32950e-02 -4.42570e-02
  2.58180e-02  5.69600e-03  1.10534e-01  1.31280e-02 -2.94600e-03
 -4.51200e-03  3.95170e-02  6.94890e-02  2.06790e-02 -6.77300e-02
 -5.76300e-03 -4.29920e-02 -1.34840e-02 -8.28010e-02 -6.67240e-02
  1.27138e-01  4.17640e-02 -2.43400e-03  6.20800e-03  1.61550e-02
 -4.47410e-02 -7.93620e-02 -3.03410e-02 -1.72100e-02  1.23390e-02
 -1.01248e-01 -9.45630e-02  1.17980e-02 -4.29240e-02 -4.27620e-02
 -3.62470e-02  7.75730e-02 -6.63590e-02 -1.12670e-02  3.29800e-03
  6.23030e-02 -9.11830e-02 -7.97050e-02  8.26050e-02  2.72000e-03
  3.18840e-02  1.26548e-01 -4.64390e-02 -3.06600e-02 -6.83800e-03
 -3.78060e

In [6]:
word_index = tokenizer.word_index

In [7]:
data = pad_sequences(sequences, maxlen=MAX_SEQUENCE_LENGTH, padding='post', truncating='post')
print(data[0])

[    1  6830    30  1202   664  2823    11    76   262   679  1290   675
   133     4     1   469     2   453    51     3     6  1364     9     2
    19   358   785     4  4149    16    33     1   754    34     9     4
  2289     7  6636  4514   582    14     5  8021 29280 14301     2    49
    41  3047   136     3  1197  1383   204    10     1    69    54     3
    84   249    57     6    89  2463   189    13   132    20    49     9
   306  2356     2    94   137   133     1  1984     6  4379     4  3752
     7   139    59    12     6    64   406    22   132     1   422  2650
     4   111    12    33   133     2    79   351     1 10943   226     4
     7   857 17860 17861   127   385   122     1   422  1562   432   287
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0   

In [8]:
VALIDATION_SPLIT = 0.2
indices = np.arange(data.shape[0])
np.random.shuffle(indices)
data = data[indices]
labels = labels[indices]
num_validation_samples = int(VALIDATION_SPLIT * data.shape[0])

x_train = data[:-num_validation_samples]
y_train = labels[:-num_validation_samples]
x_val = data[-num_validation_samples:]
y_val = labels[-num_validation_samples:]

In [16]:
EMBEDDING_DIM = 300
vocab_size = len(word_index) + 2
embedding_matrix = np.zeros((vocab_size, EMBEDDING_DIM))
for word, i in word_index.items():
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None:
        # words not found in embedding index will be all-zeros.
        embedding_matrix[i] = embedding_vector
        print(word, i)
#         print(embedding_matrix[i])
    else:
        print("no embedding for word", word)

no embedding for word the
no embedding for word and
no embedding for word i
no embedding for word to
no embedding for word a
no embedding for word was
no embedding for word my
no embedding for word of
no embedding for word in
no embedding for word for
no embedding for word is
no embedding for word it
no embedding for word they
no embedding for word with
no embedding for word you
no embedding for word that
no embedding for word this
no embedding for word on
no embedding for word we
no embedding for word me
no embedding for word have
no embedding for word he
no embedding for word so
no embedding for word had
no embedding for word very
great 26
no embedding for word but
no embedding for word are
no embedding for word be
no embedding for word at
no embedding for word not
time 32
no embedding for word all
no embedding for word were
no embedding for word as
no embedding for word out
place 37
service 38
no embedding for word will
no embedding for word an
no embedding for word up
no embedding 

owned 946
table 947
exceptional 948
salt 949
no embedding for word experiences
no embedding for word clients
no embedding for word gotten
monday 953
attentive 954
counter 955
plumbing 956
no embedding for word we've
ac 958
artist 959
no embedding for word scott
ahead 961
original 962
asking 963
desk 964
box 965
hold 966
floor 967
sign 968
additional 969
training 970
pleasure 971
white 972
no embedding for word eric
latte 974
amazon 975
wall 976
horrible 977
thinking 978
thai 979
smile 980
eye 981
no embedding for word repaired
eyebrow 983
play 984
instructor 985
send 986
seating 987
dinner 988
easily 989
no embedding for word paying
returning 991
matter 992
rob 993
helping 994
game 995
no embedding for word spots
rather 997
surprise 998
reliable 999
no embedding for word visited
no embedding for word saved
sea 1002
included 1003
no embedding for word jason
no embedding for word says
25 1006
regret 1007
cigar 1008
brake 1009
club 1010
unfortunately 1011
state 1012
beat 1013
phenomenal 1

vic 1747
craving 1748
current 1749
crystal 1750
no embedding for word k
worse 1752
bigger 1753
no embedding for word treats
no embedding for word lashes
recent 1756
traditional 1757
earth 1758
no embedding for word treatments
king 1760
bedroom 1761
performed 1762
no embedding for word bucks
payment 1764
espresso 1765
no embedding for word x
pull 1767
trouble 1768
nail 1769
wear 1770
rep 1771
terrific 1772
remove 1773
professionally 1774
combination 1775
everyday 1776
bmw 1777
deserve 1778
egg 1779
no embedding for word hoping
changing 1781
average 1782
calm 1783
jasmine 1784
slow 1785
mixed 1786
shared 1787
industry 1788
no embedding for word provides
sausage 1790
mostly 1791
fell 1792
no embedding for word dealt
sort 1794
mexican 1795
pleasantly 1796
snow 1797
no embedding for word nevada
tim 1799
tire 1800
collection 1801
otherwise 1802
ambiance 1803
grilled 1804
minor 1805
item 1806
brown 1807
concerned 1808
runs 1809
scoop 1810
no embedding for word introduced
orange 1812
yogurt 18

listed 2643
no embedding for word delish
feed 2645
superior 2646
no embedding for word stood
shades 2648
cheddar 2649
no embedding for word steps
signature 2651
partner 2652
cinnamon 2653
no embedding for word sounded
rescue 2655
fur 2656
no embedding for word babies
salted 2658
pound 2659
reschedule 2660
hype 2661
no embedding for word deserved
no embedding for word chipotle
no embedding for word beverages
no embedding for word cats
no embedding for word resolved
standing 2667
learning 2668
effective 2669
no embedding for word legs
familiar 2671
bags 2672
victor 2673
bulwark 2674
no embedding for word zach
no embedding for word shaina
automotive 2677
present 2678
responsible 2679
no embedding for word eddie
perform 2681
no embedding for word lasted
topping 2683
foodie 2684
activity 2685
length 2686
seasoned 2687
no embedding for word proceeded
silver 2689
no embedding for word jennifer
no embedding for word miguel
no embedding for word schwartz
no embedding for word ages
suggestion 26

2013 3595
no embedding for word watches
secure 3597
belly 3598
killer 3599
no embedding for word whom
no embedding for word varieties
no embedding for word spas
no embedding for word girlfriends
unsure 3604
no embedding for word reservations
cuz 3606
sexy 3607
no embedding for word brands
teaching 3609
plant 3610
no embedding for word dreikosen
dam 3612
ops 3613
no embedding for word lattes
seal 3615
no embedding for word could've
no embedding for word wished
odor 3618
no embedding for word delivers
no embedding for word tested
no embedding for word experts
no embedding for word it'll
mad 3623
cloud 3624
no embedding for word fits
greeting 3626
screw 3627
fluffy 3628
whim 3629
tomato 3630
no embedding for word g
kindly 3632
handful 3633
no embedding for word mounted
no embedding for word york
dj 3636
muscle 3637
no embedding for word andy
jungle 3639
chiropractic 3640
commitment 3641
belt 3642
olive 3643
6pm 3644
protect 3645
no embedding for word scratches
volume 3647
no embedding for

...

unaffected 44909
no embedding for word lmbo
bounded 44911
no embedding for word uberclean
no embedding for word rubin
venison 44914
no embedding for word 40lb
no embedding for word perkville
no embedding for word 5747
no embedding for word 6425032
no embedding for word jolyn's
rancid 44920
no embedding for word doggo's
no embedding for word diva's
no embedding for word wit's
no embedding for word 85284
no embedding for word stripclubs
no embedding for word marshmello
no embedding for word 5'1
no embedding for word southsider
no embedding for word youngest's
constellation 44930
no embedding for word weeklies
no embedding for word zillion's
no embedding for word sge
55th 44934
sectioning 44935
no embedding for word soooooooooooooooooooo
no embedding for word gooooooooooood
no embedding for word girlfried
no embedding for word spottted
no embedding for word replaceed
no embedding for word mckinnon
no embedding for word availing
no embedding for word jumba
no embedding for word 'bacon'
no 

advancement 45957
no embedding for word muffy
no embedding for word hoppi
no embedding for word chocomint
plunger 45961
no embedding for word donte
no embedding for word reez
no embedding for word call'
no embedding for word had'
no embedding for word 'job'
breech 45967
no embedding for word instyle
no embedding for word carley
no embedding for word explantions
no embedding for word farnaz
no embedding for word 'pleasant'
no embedding for word tdf
no embedding for word campari
no embedding for word scamed
no embedding for word schmooze
no embedding for word alexandria
no embedding for word desensitizing
no embedding for word tourgue
no embedding for word deisel
no embedding for word compleaty
no embedding for word dmy
no embedding for word rankings
no embedding for word plussssss
macro 45985
omnivorous 45986
no embedding for word hielo
no embedding for word kyles
no embedding for word profrssional
no embedding for word manzana
no embedding for word naranja
no embedding for word colombi

no embedding for word mexicoke
no embedding for word tnm
nutmeg 47215
no embedding for word frappacrap
no embedding for word 17yr
no embedding for word overstating
scrupulous 47219
no embedding for word laughin
no embedding for word awwwwesome
parkour 47222
no embedding for word rehabilitator
paucity 47224
modality 47225
no embedding for word salchi
no embedding for word phos
audiobook 47228
no embedding for word reccommended
no embedding for word veganforlife
no embedding for word lxvesstudios
no embedding for word cutsnroses
no embedding for word besthaircut
no embedding for word cronic
no embedding for word scorchingly
ceaseless 47236
stylishly 47237
no embedding for word facecloths
expressionless 47239
no embedding for word hot's
no embedding for word tushar
no embedding for word stumbles
shone 47243
no embedding for word i'ld
no embedding for word manifestations
no embedding for word penelope
no embedding for word hays
no embedding for word lovemy
no embedding for word eatable
no 

sequined 48250
no embedding for word rns
pajama 48252
advisable 48253
no embedding for word thanky
adverse 48255
no embedding for word 2699
no embedding for word 3399
wavefront 48258
arthroscopic 48259
no embedding for word anton
no embedding for word malinda
no embedding for word profectionists
no embedding for word untinted
no embedding for word nly
no embedding for word todayand
no embedding for word preorders
no embedding for word soook
no embedding for word jannie
gds 48269
no embedding for word malti
no embedding for word furkids
no embedding for word kaput
no embedding for word expecte
no embedding for word deglanding
no embedding for word 10years
no embedding for word manuka
blot 48277
heath 48278
no embedding for word eliot
no embedding for word eduacated
no embedding for word paychecks
no embedding for word portugal
quartier 48283
no embedding for word quartiers
hare 48285
no embedding for word sunspots
no embedding for word yogurtlands
no embedding for word mouler
no embeddi

postnatal 49320
no embedding for word huffing
no embedding for word 75b
no embedding for word hendertucky
no embedding for word z71
midyear 49325
no embedding for word longness
no embedding for word g2r
no embedding for word kolache's
glorified 49329
purebred 49330
no embedding for word egged
no embedding for word takeovers
no embedding for word wrestles
no embedding for word cadi
milling 49335
no embedding for word cales
saison 49337
no embedding for word telsa
319 49339
vit 49340
skewing 49341
no embedding for word roxanne's
'03 49343
no embedding for word cwt's
no embedding for word micros
no embedding for word 45lb
pressurized 49347
no embedding for word holey
no embedding for word honeys
no embedding for word booziest
no embedding for word aze
no embedding for word severson
no embedding for word benn
insertion 49354
no embedding for word corse
no embedding for word superspinatus
no embedding for word infraspinatus
no embedding for word terres
no embedding for word supscapularis
no

In [17]:
print(embedding_matrix[26])

[ 1.21059999e-01  8.49299971e-03  8.42709988e-02 -7.59269968e-02
  1.51469996e-02  1.76650006e-02  9.43880007e-02 -2.17109993e-02
 -1.71150006e-02 -8.79250020e-02 -2.22430006e-02  3.66830006e-02
  1.46789998e-02  3.82880010e-02 -1.17499996e-02  1.32952005e-01
  6.16939999e-02 -8.12800042e-03 -2.82290000e-02 -4.56579998e-02
  6.11380003e-02  6.67600008e-03 -7.00000003e-02 -5.95100001e-02
  1.78970005e-02  9.44489986e-02 -4.58809994e-02  3.77999997e-04
 -3.78479995e-02  1.05512001e-01  1.86410006e-02 -6.21099994e-02
  8.90119970e-02  2.07819995e-02 -9.05799959e-03 -3.02430000e-02
  8.85699969e-03  3.33839990e-02 -4.45579998e-02  6.93899998e-03
  2.53079999e-02  1.04189999e-02 -4.65670004e-02 -2.54689995e-02
  8.78349990e-02  6.54750019e-02 -2.79649999e-02 -3.55469994e-02
 -2.66679991e-02  9.41499993e-02 -6.57700002e-03 -5.88340014e-02
 -1.22187003e-01 -7.47689977e-02  9.61299986e-03  2.22859997e-02
 -5.07390015e-02 -6.64580017e-02  2.70639993e-02 -4.49989997e-02
  4.20479998e-02  5.92710

In [18]:
num_words = len(word_index) + 1
embedding_layer = Embedding(input_dim=num_words,
                            output_dim=EMBEDDING_DIM,
                            input_length=MAX_SEQUENCE_LENGTH,
                            trainable=False)


In [19]:
model = Sequential()
model.add(embedding_layer)
model.add(Conv1D(128, 5, activation='relu'))
model.add(GlobalMaxPooling1D())
model.add(Dense(1000, activation='relu'))
model.add(Dense(5, activation='sigmoid'))

In [20]:
model.compile(loss='categorical_crossentropy',
              # loss='binary_crossentropy',
              # optimizer='rmsprop',
              optimizer='adam',
              metrics=['acc'],)

In [21]:
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_2 (Embedding)      (None, 1000, 300)         14882100  
_________________________________________________________________
conv1d_2 (Conv1D)            (None, 996, 128)          192128    
_________________________________________________________________
global_max_pooling1d_2 (Glob (None, 128)               0         
_________________________________________________________________
dense_3 (Dense)              (None, 1000)              129000    
_________________________________________________________________
dense_4 (Dense)              (None, 5)                 5005      
Total params: 15,208,233
Trainable params: 326,133
Non-trainable params: 14,882,100
_________________________________________________________________


In [23]:
model.fit(x_train, y_train,
          batch_size=128,
          epochs=10,
          validation_data=(x_val, y_val), verbose=2,)


Train on 53895 samples, validate on 13473 samples
Epoch 1/10


KeyboardInterrupt: 

In [24]:
from keras.datasets import imdb
(x_train, y_train), (x_text, y_text) = imdb.load_data(num_words=10000)

In [25]:
print(x_train[0])

[1, 14, 22, 16, 43, 530, 973, 1622, 1385, 65, 458, 4468, 66, 3941, 4, 173, 36, 256, 5, 25, 100, 43, 838, 112, 50, 670, 2, 9, 35, 480, 284, 5, 150, 4, 172, 112, 167, 2, 336, 385, 39, 4, 172, 4536, 1111, 17, 546, 38, 13, 447, 4, 192, 50, 16, 6, 147, 2025, 19, 14, 22, 4, 1920, 4613, 469, 4, 22, 71, 87, 12, 16, 43, 530, 38, 76, 15, 13, 1247, 4, 22, 17, 515, 17, 12, 16, 626, 18, 2, 5, 62, 386, 12, 8, 316, 8, 106, 5, 4, 2223, 5244, 16, 480, 66, 3785, 33, 4, 130, 12, 16, 38, 619, 5, 25, 124, 51, 36, 135, 48, 25, 1415, 33, 6, 22, 12, 215, 28, 77, 52, 5, 14, 407, 16, 82, 2, 8, 4, 107, 117, 5952, 15, 256, 4, 2, 7, 3766, 5, 723, 36, 71, 43, 530, 476, 26, 400, 317, 46, 7, 4, 2, 1029, 13, 104, 88, 4, 381, 15, 297, 98, 32, 2071, 56, 26, 141, 6, 194, 7486, 18, 4, 226, 22, 21, 134, 476, 26, 480, 5, 144, 30, 5535, 18, 51, 36, 28, 224, 92, 25, 104, 4, 226, 65, 16, 38, 1334, 88, 12, 16, 283, 5, 16, 4472, 113, 103, 32, 15, 16, 5345, 19, 178, 32]


In [26]:
print(x_train[0].decode)

AttributeError: 'list' object has no attribute 'decode'